In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        pass

In [ ]:
import os
import warnings
warnings.filterwarnings('ignore')

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt


In [ ]:
# cat '/kaggle/input/rice-image-dataset/Rice_Image_Dataset/Rice_Citation_Request.txt'

In [ ]:
os.listdir(path)

In [ ]:
path='/kaggle/input/rice-image-dataset/Rice_Image_Dataset'

In [ ]:
def create_dataset(folders, path, max_images_per_label=1000):
    data = {'imgpath': [], 'labels': []}
    
    for folder in folders:
        folderpath = os.path.join(path, folder)
        files = os.listdir(folderpath)
        
        # Her bir klasörden sadece max_images_per_label kadar görsel alıyoruz
        selected_files = files[:max_images_per_label]
        
        for file in selected_files:
            filepath = os.path.join(folderpath, file)
            data['imgpath'].append(filepath)
            data['labels'].append(folder)

    dataset = pd.DataFrame(data)
    return dataset

#  Ben Her  piniç  çeşidi için 1000 veri yeterli diye düşündüm ononu yüzündeb böyle bir işlem yaptım

In [ ]:
folders1 = ['Arborio', 'Basmati', 'Ipsala', 'Jasmine', 'Karacadag'] 
df=create_dataset(folders1,path)
df.head()

In [ ]:
import cv2
import matplotlib.pyplot as plt
for index, row in df.sample(7).iterrows():
    # Resmi yükle
    img = cv2.imread(row['imgpath'])
    
    # OpenCV resmi RGB formatına dönüştür
    img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    
    # Resmi matplotlib ile göster
    plt.figure(figsize=(6, 6))
    plt.imshow(img_rgb)
    plt.title(row['labels'])
    plt.axis('off')
    plt.show()

# Verilerin Görselleştirilmesi

In [ ]:
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
import plotly.express as px

sayi = df['labels'].value_counts() #hurma türe göre sayisi 
 
# Plotly ile hurma dağılımını görselleştirme
fig=px.bar(x=sayi.index,  #6 indexi var
           y=sayi.values, # sayisi 
           color=sayi.index, # rekleri yine sayisina göre
           labels={'x': 'Çeşitler','y': 'Toplam Sayı'}, #label yazdırma
           title='Pirinç Çeşitleri Grafiği', #başlık 
           template='plotly_dark') # arkapılan 

fig.show()


fig = px.pie(names=sayi.index,
             values=sayi.values,
             title='Pirinç Dağılımı',
             labels={'names': 'Hurma',
                     'values': 'Toplam Sayı'},
             template='plotly_white')
fig.show()

# Modeling 

![cnn](https://docs.ecognition.com/v9.5.0/Resources/Images/ECogUsr/UG_CNN_scheme.png)

In [ ]:
from sklearn.model_selection import train_test_split

# Önce train ve geçici test (val+test) ayırma
train_df, temp_df = train_test_split(df, test_size=0.2, random_state=42)

# Sonra geçici test verisini (val+test) val ve test olarak ayırma
val_df, test_df = train_test_split(temp_df, test_size=0.5, random_state=42)

train_df.shape, val_df.shape, test_df.shape

In [ ]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
seed = 42
batch_size = 128
img_size = (224, 224)

generator = ImageDataGenerator(rescale = 1./255)

train_data = generator.flow_from_dataframe(train_df, x_col = 'imgpath', y_col = 'labels', 
                                           color_mode = 'rgb', class_mode = 'categorical', 
                                           batch_size = batch_size, target_size = img_size, 
                                           shuffle = True, seed = seed)

val_data = generator.flow_from_dataframe(val_df, x_col = 'imgpath', y_col = 'labels', 
                                         color_mode = 'rgb', class_mode = 'categorical', 
                                         batch_size = batch_size, target_size = img_size, 
                                         shuffle = False)

test_data = generator.flow_from_dataframe(test_df, x_col = 'imgpath', y_col = 'labels', 
                                          color_mode = 'rgb', class_mode = 'categorical', 
                                          batch_size = batch_size, target_size = img_size, 
                                          shuffle = False)

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.losses import CategoricalCrossentropy

model = Sequential()
model.add(Input(shape=(224, 224, 3)))
model.add(Conv2D(32, kernel_size=(3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(64, kernel_size=(3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(128, kernel_size=(3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(256, kernel_size=(3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Flatten())
model.add(Dense(128, activation='relu'))

model.add(Dense(5, activation='softmax'))  # 5 kategori

# Modelin derlenmesi
model.compile(optimizer='adam', loss=CategoricalCrossentropy(), metrics=['accuracy'])#kategorik etiketler varsa loss = 'CategoricalCrossentropy()'

In [ ]:
import warnings
warnings.filterwarnings('ignore')
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau

model_es = EarlyStopping(monitor = 'val_loss', mode = 'min', patience = 2, restore_best_weights = True)
model_rlr = ReduceLROnPlateau(monitor = 'val_loss', factor = 0.2, patience = 1, mode = 'min')

history = model.fit(train_data, validation_data = val_data, 
                    epochs = 10, callbacks = [model_es, model_rlr])

In [ ]:
model.save('rice_model.h5')

In [ ]:
# Eğitim ve Doğrulama Kaybı
plt.plot(history.history['loss'], label='Eğitim Kaybı')
plt.plot(history.history['val_loss'], label='Doğrulama Kaybı')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()
plt.show()

# Eğitim ve Doğrulama Doğruluğu
plt.plot(history.history['accuracy'], label='Eğitim Doğruluğu')
plt.plot(history.history['val_accuracy'], label='Doğrulama Doğruluğu')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend()
plt.show()

In [ ]:
import seaborn as sns
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay

# Model ile tahmin yapma
y_pred = model.predict(test_data, steps=test_data.samples // test_data.batch_size + 1)
y_pred_classes = np.argmax(y_pred, axis=1)  # Tahmin edilen sınıflar

# Gerçek etiketleri alma
y_true = test_data.classes  # Gerçek etiketler

# Confusion Matrix hesaplama
cm = confusion_matrix(y_true, y_pred_classes)

# Confusion Matrix'i görselleştirme
fig, ax = plt.subplots(figsize=(10, 8))
plt.title('Confusion matrixisimiz')
disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=test_data.class_indices.keys())
disp.plot(cmap=plt.cm.Blues, ax=ax)
plt.show()

In [ ]:
class_names = list(test_data.class_indices.keys())
report = classification_report(y_true, y_pred_classes, target_names=class_names)
print(report)

In [ ]:
test_results = model.evaluate(test_data, verbose = 0)

print(f'Test Loss: {test_results[0]:.5f}')
print(f'Test Accuracy: {(test_results[1] * 100):.2f}%')

In [ ]:
model.summary()

****Conuç olarak CNN ile modelimiz Doğruluk olranı %95-99 arasına aldık
ve bu modeli kayıt edip mobil bir programda kullanıcağız***

EK olarak  Daha önce Yaptığım modelden yola çıkarak aynı sonucu alabilirmiyim ? 

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Input, Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.losses import CategoricalCrossentropy



import tensorflow as tf
from tensorflow.keras import layers, models
model2 = models.Sequential()

# Evrişimsel katmanlar(Conv) ve havuzlama(pooling) katmanları

model2.add(Input(shape=(224, 224, 3)))
model2.add(Conv2D(32, kernel_size=(3, 3), activation='relu'))
model2.add(MaxPooling2D(pool_size=(2, 2)))

model2.add(layers.Conv2D(64, (3, 3), activation='relu'))
model2.add(layers.MaxPooling2D((2, 2)))
model2.add(layers.Dropout(0.25))

model2.add(layers.Conv2D(128, (3, 3), activation='relu'))
model2.add(layers.MaxPooling2D((2, 2)))
model2.add(layers.Dropout(0.25))

model2.add(layers.Conv2D(128, (3, 3), activation='relu'))
model2.add(layers.MaxPooling2D((2, 2)))
model2.add(layers.Dropout(0.25))

model2.add(layers.Conv2D(256, (3, 3), activation='relu'))
model2.add(layers.MaxPooling2D((2, 2)))
model2.add(layers.Dropout(0.25))

# Düzleştirme ve tam bağlı katmanlar
model2.add(layers.Flatten())  # düzleştirme

model2.add(layers.Dense(512, activation='relu'))
model2.add(layers.Dropout(0.5))  # Yüksek dropout oranı, tam bağlı katmanlarda aşırı öğrenmeyi azaltabilir
model2.add(layers.Dense(5, activation='softmax'))  # Çıkış katmanı: 9 sınıf için # çeşit sayımıza göre 

model2.compile(optimizer='adam',loss=CategoricalCrossentropy(),metrics=['accuracy'])

import warnings
warnings.filterwarnings('ignore')
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau

model_es = EarlyStopping(monitor = 'val_loss', mode = 'min', patience = 2, restore_best_weights = True)
model_rlr = ReduceLROnPlateau(monitor = 'val_loss', factor = 0.2, patience = 1, mode = 'min')

history2 = model2.fit(train_data, validation_data = val_data, 
                    epochs = 10, callbacks = [model_es, model_rlr])

In [ ]:
model2.save('price_model2.h5')

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix, classification_report

# Test veri kümesi üzerinden tahmin yapma
test_data = generator.flow_from_dataframe(
    dataframe=test_df,
    x_col='imgpath',
    y_col='labels',
    color_mode='rgb',
    class_mode='categorical',
    batch_size=batch_size,
    target_size=img_size,
    shuffle=False
)

# Model ile tahminler
y_pred_probs = model2.predict(test_data)
y_pred = np.argmax(y_pred_probs, axis=1)  # En yüksek olasılığa sahip sınıfı seç
y_true = test_data.classes  # Gerçek etiketler

# Confusion Matrix
cm = confusion_matrix(y_true, y_pred)

# Plot Confusion Matrix
plt.figure(figsize=(10, 7))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', xticklabels=test_data.class_indices.keys(), yticklabels=test_data.class_indices.keys())
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title('Confusion Matrix')
plt.show()

# Classification Report
print("Classification Report:")
print(classification_report(y_true, y_pred, target_names=test_data.class_indices.keys()))
